### The number of $F_{q^r}$-rational points on a curve over $F_q$

Main reference: MSX-2017, *A bootstrap for the number of $F_{q^r}$-rational points on a curve over $F_q$*
(S. Molina, N. Sayols, S. Xambó, https://mat-web.upc.edu/people/sebastia.xambo/Preprints/2017-Molina-Sayols-Xambo.pdf).

By *curve over* $F_q$ we understand (unless explicitly stated otherwise) 
*a smooth absolutely irreducible projective curve over the finite field $F_q$ of cardinal $q$*.

The aim of this notebook is to explain an implementarion of a fast algorithm 
that finds, for any given $r$, the number $X_r$ of $F_{q^r}$-rational points 
on a curve $C$ defined over $F_q$
assuming $X_1,\dotsc,X_g$ are known, where $g$ is the genus of $C$.

The rational field is denoted $Q\_$. For any integer $x$, $x>>Q\_$ 
is the inclusion of the integer $x$ in $Q\_$.

#### Ingredients

The *Hasse-Weil-Serre upper bound* (HWS)for the maximum number $N_q(g)$ of
of $F_q$-rational points on a curves $C/F_q$ of genus $g$
(Serre-1983a, Serre-1983b, Serre-1984):

* $N_q(g)\le q+1 + g \lfloor 2\sqrt{q}\rfloor$.


 
A curve $C/F_q$  is said to be *maximal* if 
the number of its $F_q$ points equals $N_q(g)$.

For historical aspects and background, we refer
to the excellent surveys Torres-2008, vdGeer-2015, and the 
many references provided there. 
The general context provided by the
Weil conjectures is outlined in Hartshorne-1983,
Appendix C.

#### `XN(q,X,k)`

**Input:** $q$

**Output:** The list $[X_1\dotsc,X_g,\dotsc,X_k]$.

In [1]:
from PyM import *

def XN(q,X,k):
    g = len(X)
    if k<=g: return X[:k]
    X = [0]+X           # trick so that X[j] refers to F_{q^j}
    X = [x>>Q_ for x in X]
    S = [q**(j)+1-X[j] for j in range(1,g+1)] # Newton sums
    S = [0]+S           # similar trick
    # Computation of c1,...,cg; set c0=1 
    c = [1>>Q_]           
    for j in range(1,g+1):
        cj = S[j]
        for i in range(1,j):
            cj += c[i]*S[j-i]
        c += [-cj/j]
    # Add c_{g+i}, for i=1,...,g
    for i in range(1,g+1):
        c += [q**i*c[g-i]]
    # Find Sj for j = g+1,...,k
    for j in range(g+1,k+1):
        if j>2*g:
            Sj=0
        else: 
            Sj = j*c[j]
        for i in range(1,j):
            if i>2*g: break
            Sj += c[i]*S[j-i]
        S += [-Sj]
    # Find X[i] for i = g+1,...,k
    for i in range(g+1,k+1):
        X += [q**i+1-S[i]]
    return vector(X[1:])

q=2
m=15
M = matrix([XN(q,[1],m), XN(q,[2],m), XN(q,[3],m), XN(q,[4],m),XN(q,[5],m)])
M1 = transpose(M)
show(M1)

[[1	2	3	4	5]
 [5	8	9	8	5]
 [13	14	9	4	5]
 [25	16	9	16	25]
 [41	22	33	44	25]
 [65	56	81	56	65]
 [113	142	129	116	145]
 [225	288	225	288	225]
 [481	518	513	508	545]
 [1025	968	1089	968	1025]
 [2113	1982	2049	2116	1985]
 [4225	4144	3969	4144	4225]
 [8321	8374	8193	8012	8065]
 [16385	16472	16641	16472	16385]
 [32513	32494	32769	33044	33025]] 



In [9]:
def Nqg(q,g):
    return q + 1 + g*floor(2*sqrt(q))

q=2
m=15
M2 = vector([Nqg(q**i,1) for i in range(1,m+1)])
show(M2)

[5, 9, 14, 25, 44, 81, 151, 289, 558, 1089, 2139, 4225, 8374, 16641, 33131] 



#### Implementation of an algorithm of Deuring

We refer to Deuring's algorithm that lists the possible cardinals $\#E(F_q)$
of the elliptic curves $E/F_q$. 

Our main reference here has been "Abelian varieties over finite fields", by
W. C. Waterhouse *Annales Scientiiques de l'École Normale Supérieure*, volume 2, pages 521-560, 1969.

We have split the computation in two parts: the function `Deuring_offsets(q)` 
(which computes the list of integers $t$ in the segment $[-m,m]$, $m=\lfloor 2\sqrt{q}\rfloor$,
such that $\#E(F_q)=q+1-t$ for some $E$), and `Deuring_set(q)`, that outputs the list in question.  


In [3]:
def Deuring_offsets(q):
    P = prime_factors(q)  # prime_factors(12) => [2, 2, 3]
    p = P[0]; n = len(P)
    m = int(2*sqrt(q))
    D = [t for t in range(-m,m+1) if gcd(p,t)==1]
    if n%2==0: 
        r = p**(n//2)
        D += [-2*r,2*r] 
        if p%3 != 1: 
            D += [-r,r]
    if n%2 and (p==2 or p==3):
        r = p**((n+1)//2)
        D += [-r,r]
    if n%2 or (n%2==0 and p%4!=1):
        D += [0]
    return sorted([t for t in D])

def Deuring_set(q):
    D =Deuring_offsets(q)
    return [t+q+1 for t in D]

Q = [2,3,4,5,7,8,9,11,13,16,17,19]
for q in Q:
    m = int(2*sqrt(q))
    D = Deuring_set(q)
    show([q,2*m+1-len(D)],[q+1-m,q+1+m], D)


[2, 0] [1, 5] [1, 2, 3, 4, 5] 

[3, 0] [1, 7] [1, 2, 3, 4, 5, 6, 7] 

[4, 0] [1, 9] [1, 2, 3, 4, 5, 6, 7, 8, 9] 

[5, 0] [2, 10] [2, 3, 4, 5, 6, 7, 8, 9, 10] 

[7, 0] [3, 13] [3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13] 

[8, 2] [4, 14] [4, 5, 6, 8, 9, 10, 12, 13, 14] 

[9, 0] [4, 16] [4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16] 

[11, 0] [6, 18] [6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18] 

[13, 0] [7, 21] [7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21] 

[16, 4] [9, 25] [9, 10, 12, 13, 14, 16, 17, 18, 20, 21, 22, 24, 25] 

[17, 0] [10, 26] [10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26] 

[19, 0] [12, 28] [12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28] 



In [4]:
def Serre(q, g=1):
    D = ifactor(q) # ifactor(12) => {2: 2, 3: 1}
    if len(D)>1:
        return 'Serre: {} is not a prime power'.format(q)
    p = list(D)[0]
    e = D[p] # q = p^e
    m = int(2*sqrt(q)) # gm is the HWS bound
    if g==1:
        if e%2 and e>=3 and m%p==0: return q+m
        else: return q+m+1
    if g==2:
        if q==4: return 10
        if q==9: return 20
        if e%2==0: return q+1+2*m
        def special(s):
            if m%p==0 or is_square(s-1) or \
                         is_square(4*s-3) or \
                         is_square(4*s-7): 
                return True
            else: return False
        if special(q):
            if 2*sqrt(q)-m > (sqrt(5)-1)/2: return q+2*m
            else: return q+2*m-1
        return q+1+2*m
    if g==3:
        P = [2,3,4,5,7,8,9]
        T={2:7,3:10,4:14,5:16,7:20,8:24,9:28}
        if P.count(q): return T[q]
    return "Serre: I do not know the value of N({},{})".format(q,g)

for q in Q:
    print("q =",q,": ",Serre(q), Serre(q,2), Serre(q,3))
    

                                                            
    

q = 2 :  5 6 7
q = 3 :  7 8 10
q = 4 :  9 10 14
q = 5 :  10 12 16
q = 7 :  13 16 20
q = 8 :  14 18 24
q = 9 :  16 20 28
q = 11 :  18 24 Serre: I do not know the value of N(11,3)
q = 13 :  21 26 Serre: I do not know the value of N(13,3)
q = 16 :  25 33 Serre: I do not know the value of N(16,3)
q = 17 :  26 32 Serre: I do not know the value of N(17,3)
q = 19 :  28 36 Serre: I do not know the value of N(19,3)
